In [1]:
using DifferentialEquations
using Sundials

In [ ]:
function F(out, dz, z, p, t)
    out[1] = dz[1] - 2*z[1]*(z[3]^2 + z[4]^2) + (z[1]^2 + z[2]^2)*2*z[3] # x' = dx/dt = x' - 2x + 2u
    out[2] = dz[2] - 2*z[2]*(z[3]^2 + z[4]^2) + (z[1]^2 + z[2]^2)*2*z[4] # x' = dy/dt = y' - 2y + 2v
    out[3] = 1 - z[1] - z[3] # 1 - x - u
    out[4] = - z[2] - z[4] # - y - v
end

H(z, w) = 1 - z - w
g(z) = 1-z # for computing initial conditions and plotting

initial_conditions = []
radius = 1/18
for θ in 0:0.1:2π
    z₀ = radius * exp.(im*θ)
    x₀ = real(z₀)
    y₀ = imag(z₀)
    u₀ = real(g(z₀))
    v₀ = imag(g(z₀))
    dx₀ = 2*x₀*(u₀^2 + v₀^2) - (x₀^2 + y₀^2)*2*u₀
    dy₀ = 2*y₀*(u₀^2 + v₀^2) - (x₀^2 + y₀^2)*2*v₀
    du₀ = - 2*y₀*(u₀^2 + v₀^2) + (x₀^2 + y₀^2)*2*v₀
    dv₀ = - 2*y₀*(u₀^2 + v₀^2) + (x₀^2 + y₀^2)*2*v₀
    push!(initial_conditions, [[dx₀; dy₀; du₀; dv₀], [x₀; y₀; u₀; v₀]])
end

tval = 1.2
tstops = collect(0:0.03:tval)
prob = DAEProblem(F, initial_conditions[1][1], initial_conditions[1][2], tval, tstops=tstops, differential_vars=[true, true, false, false])
function prob_func(prob, i, repeat)
  remake(prob, du0=initial_conditions[i][1], u0=initial_conditions[i][2])
end

ensemble_prob = EnsembleProblem(prob, prob_func=prob_func)
sim = solve(ensemble_prob, IDA(), EnsembleDistributed(), trajectories=length(initial_conditions))

In [3]:
using Plots
plotly()

# RINGS
N = 200
x = collect(Float16, range(-2.2, length=N, stop=3.2))
y = collect(Float16, range(-2, length=N, stop=2))
h(x, y, u, v) = -log(x^2 + y^2)/2 -log(u^2 + v^2)/2
param(x, y) = h(x, y, real(g(x+y*im)), imag(g(x+y*im)))
p = plot(x, y, param, st = :surface, legend = false, axis = true, size=(800, 800))

┌ Warning: For saving to png with the `Plotly` backend `PlotlyBase` and `PlotlyKaleido` need to be installed.
│   err =
│    ArgumentError: Package PlotlyKaleido not found in current path.
│    - Run `import Pkg; Pkg.add("PlotlyKaleido")` to install the PlotlyKaleido package.
└ @ Plots ~/.julia/packages/Plots/bMtsB/src/backends.jl:552


In [4]:
ϵ = 1e-14 # close enough to call equal
for i in 1:length(tstops)
    tval = tstops[i]
    if any(isnothing(findfirst(abs.(sol.t .- tval) .< ϵ)) for sol in sim)
        break
    end
    
    # plot ring
    xs = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][1] for sol in sim]
    ys = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][2] for sol in sim]
    us = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][3] for sol in sim]
    vs = [sol.u[findfirst(abs.(sol.t .- tval) .< ϵ)][4] for sol in sim]
    zs = [1/100 + h(xs[idx], ys[idx], us[idx], vs[idx]) for idx in 1:length(sim)]
    plot!(xs, ys, zs, lc = RGB(0.1, 1, 1-i * 1/length(tstops)), lw = 3)
end

p